# Récupération de l'ORM!

In [1]:
from sqlalchemy import create_engine
from sqlalchemy.ext.declarative import declarative_base
from sqlalchemy.orm import sessionmaker
from sqlalchemy import Table, Column, Integer, ForeignKey
from sqlalchemy.orm import relationship
import pandas as pd

In [2]:
dbPath = 'recopytex.db'
engine = create_engine('sqlite:///%s' % dbPath, echo=True)
Base = declarative_base(engine)

In [3]:
class Student(Base):
    """"""
    __tablename__ = 'student'
    __table_args__ = {'autoload':True}
    
    scores = relationship("Score", backref="student")
    
    @property
    def fullname(self):
        if self.surname:
            return ' '.join([self.name.upper(), self.surname.capitalize()])

        return self.name.upper()
                            
    def __repr__(self):
        return f"<Student {self.fullname}>"
    
    def to_df(self, columns = ["id", "name", "surname", "fullname", "tribe_id"]):
        cara_dict = {c:self.__getattribute__(c) for c in columns}
        return pd.DataFrame.from_dict([cara_dict])
    
    def score_df(self, with_self=True):
        scs_df = pd.concat([sc.to_df() for sc in seld.scores])
        if with_self:
            self_df = self.to_df()
            return pd.merge(scs_df, self_df, left_on="student_id", right_on="id")
        else:
            return scs_df
    

class Tribe(Base):
    """"""
    __tablename__ = 'tribe'
    __table_args__ = {'autoload':True}
    
    students = relationship("Student", backref="tribe")
    evals = relationship("Eval", backref="tribe")

    def __repr__(self):
        return f"<Tribe {self.name}>"
    
    def to_df(self, columns = ["id", "name", "grade"]):
        cara_dict = {c:self.__getattribute__(c) for c in columns}
        return pd.DataFrame.from_dict([cara_dict])
    
    def students_df(self, columns=["id", "name", "surname", "fullname", "tribe_id"]):
        dfs = []
        for s in self.students:
            dfs.append(s.to_df())
        return pd.concat(dfs)

class Eval(Base):
    """"""
    __tablename__ = 'eval'
    __table_args__ = {'autoload':True}
    
    exercises = relationship("Exercise", backref="Eval")
    
    def __repr__(self):
        return f"<Eval {self.name} for Tribe{self.tribe_id}>"
    
    @property
    def score_rate(self):
        return sum([ex.score_rate for ex in self.exercises])

class Exercise(Base):
    """"""
    __tablename__ = 'exercise'
    __table_args__ = {'autoload':True}
    
    questions = relationship("Question", backref="exercise")
    
    def __repr__(self):
        return f"<Exercise {self.name} for Eval{self.eval_id}>"
    
    @property
    def score_rate(self):
        return sum([q.score_rate for q in self.questions])

class Question(Base):
    """"""
    __tablename__ = 'question'
    __table_args__ = {'autoload':True}
    
    scores = relationship("Score", backref="question")
    
    def __repr__(self):
        return f"<Question {self.name} for Exercise{self.exercise_id}>"    
    
    def to_df(self,\
              columns = ["id", "name", "score_rate",\
                         "is_leveled", "exercise_id",\
                         "competence", "domain", "comment"],\
             ):
        cara_dict = {c:self.__getattribute__(c) for c in columns}
        return pd.DataFrame.from_dict([cara_dict])

class Score(Base):
    """"""
    __tablename__ = 'score'
    __table_args__ = {'autoload':True}
    
    def to_df(self, question=True, student=True):
        score_dict = {c:self.__getattribute__(c) for c in ["student_id", "question_id", "value"]}
        score_df = pd.DataFrame.from_dict([score_dict])
        
        # pas pratique la gestion des suffixes
        # Il faudrait changer le nom des colonnes
        if question:
            qu_df = self.question.to_df()
            score_df = pd.merge(score_df, qu_df,\
                                left_on='question_id', right_on='id',\
                               suffixes=('_score', '_question'))
        
        if student:
            s_df = self.student.to_df()
            score_df = pd.merge(score_df, s_df,\
                                left_on='student_id', right_on='id',\
                               suffixes=('_score', '_student'))
        return score_df
        

2018-02-19 07:54:25,524 INFO sqlalchemy.engine.base.Engine SELECT CAST('test plain returns' AS VARCHAR(60)) AS anon_1
2018-02-19 07:54:25,525 INFO sqlalchemy.engine.base.Engine ()
2018-02-19 07:54:25,527 INFO sqlalchemy.engine.base.Engine SELECT CAST('test unicode returns' AS VARCHAR(60)) AS anon_1
2018-02-19 07:54:25,528 INFO sqlalchemy.engine.base.Engine ()
2018-02-19 07:54:25,530 INFO sqlalchemy.engine.base.Engine PRAGMA table_info("student")
2018-02-19 07:54:25,532 INFO sqlalchemy.engine.base.Engine ()
2018-02-19 07:54:25,536 INFO sqlalchemy.engine.base.Engine SELECT sql FROM  (SELECT * FROM sqlite_master UNION ALL   SELECT * FROM sqlite_temp_master) WHERE name = 'student' AND type = 'table'
2018-02-19 07:54:25,537 INFO sqlalchemy.engine.base.Engine ()
2018-02-19 07:54:25,540 INFO sqlalchemy.engine.base.Engine PRAGMA foreign_key_list("student")
2018-02-19 07:54:25,541 INFO sqlalchemy.engine.base.Engine ()
2018-02-19 07:54:25,543 INFO sqlalchemy.engine.base.Engine SELECT sql FROM  (

2018-02-19 07:54:25,715 INFO sqlalchemy.engine.base.Engine ()
2018-02-19 07:54:25,716 INFO sqlalchemy.engine.base.Engine PRAGMA index_list("score")
2018-02-19 07:54:25,717 INFO sqlalchemy.engine.base.Engine ()
2018-02-19 07:54:25,718 INFO sqlalchemy.engine.base.Engine SELECT sql FROM  (SELECT * FROM sqlite_master UNION ALL   SELECT * FROM sqlite_temp_master) WHERE name = 'score' AND type = 'table'
2018-02-19 07:54:25,719 INFO sqlalchemy.engine.base.Engine ()


In [4]:
def loadSession():
    """"""
    metadata = Base.metadata
    Session = sessionmaker(bind=engine)
    session = Session()
    return session

In [5]:
session = loadSession()

In [6]:
tribes = session.query(Tribe).all()

2018-02-19 07:54:25,781 INFO sqlalchemy.engine.base.Engine BEGIN (implicit)
2018-02-19 07:54:25,783 INFO sqlalchemy.engine.base.Engine SELECT tribe.id AS tribe_id, tribe.name AS tribe_name, tribe.grade AS tribe_grade 
FROM tribe
2018-02-19 07:54:25,784 INFO sqlalchemy.engine.base.Engine ()


In [7]:
t = tribes[0]
t

<Tribe 302>

In [8]:
t.to_df()

grade  id name
0    3e   1  302

In [9]:
for ev in t.evals:
    print(f"Evaluation {ev.name} sur {ev.score_rate}")
    for ex in ev.exercises:
        print(f"Ex {ex.name} sur {ex.score_rate}")
        for qu in ex.questions:
            print(f"\tQu {qu.name} {qu.comment} sur {qu.score_rate}")
    print("-"*20)

2018-02-19 07:54:25,841 INFO sqlalchemy.engine.base.Engine SELECT eval.id AS eval_id, eval.name AS eval_name, eval.term AS eval_term, eval.type AS eval_type, eval.comment AS eval_comment, eval.tribe_id AS eval_tribe_id 
FROM eval 
WHERE ? = eval.tribe_id
2018-02-19 07:54:25,843 INFO sqlalchemy.engine.base.Engine (1,)
2018-02-19 07:54:25,847 INFO sqlalchemy.engine.base.Engine SELECT exercise.id AS exercise_id, exercise.name AS exercise_name, exercise.eval_id AS exercise_eval_id, exercise.date AS exercise_date, exercise.comment AS exercise_comment 
FROM exercise 
WHERE ? = exercise.eval_id
2018-02-19 07:54:25,852 INFO sqlalchemy.engine.base.Engine (1,)
2018-02-19 07:54:25,858 INFO sqlalchemy.engine.base.Engine SELECT question.id AS question_id, question.name AS question_name, question.score_rate AS question_score_rate, question.is_leveled AS question_is_leveled, question.exercise_id AS question_exercise_id, question.competence AS question_competence, question.domain AS question_domain, q

Evaluation DS3 sur 17.0
Ex 1 -QCM sur 4
	Qu   sur 4
Ex 2 sur 5.0
	Qu  Explications des calculs sur 1.5
	Qu  Formule tableur sur 1
	Qu  Choix des opérations sur 1
	Qu  Manipulation des grands nombres sur 0.5
	Qu  Comparaison sur 1
Ex 3 sur 5
	Qu 1 Démontrer parallèle sur 1
	Qu 2 Reconnaître Thalès sur 1
	Qu 2 Calculer EC sur 1
	Qu 2 Rédaction sur 1
	Qu 2 Conversions sur 1
Ex 4 sur 3
	Qu  Utiliser les bonnes informations sur 1
	Qu  Choix des calculs sur 1
	Qu  Reconnaître fractions sur 1
--------------------
2018-02-19 07:54:25,941 INFO sqlalchemy.engine.base.Engine SELECT exercise.id AS exercise_id, exercise.name AS exercise_name, exercise.eval_id AS exercise_eval_id, exercise.date AS exercise_date, exercise.comment AS exercise_comment 
FROM exercise 
WHERE ? = exercise.eval_id
2018-02-19 07:54:25,944 INFO sqlalchemy.engine.base.Engine (14,)
2018-02-19 07:54:25,947 INFO sqlalchemy.engine.base.Engine SELECT question.id AS question_id, question.name AS question_name, question.score_rate A

2018-02-19 07:54:26,012 INFO sqlalchemy.engine.base.Engine SELECT question.id AS question_id, question.name AS question_name, question.score_rate AS question_score_rate, question.is_leveled AS question_is_leveled, question.exercise_id AS question_exercise_id, question.competence AS question_competence, question.domain AS question_domain, question.comment AS question_comment 
FROM question 
WHERE ? = question.exercise_id
2018-02-19 07:54:26,013 INFO sqlalchemy.engine.base.Engine (66,)
2018-02-19 07:54:26,015 INFO sqlalchemy.engine.base.Engine SELECT question.id AS question_id, question.name AS question_name, question.score_rate AS question_score_rate, question.is_leveled AS question_is_leveled, question.exercise_id AS question_exercise_id, question.competence AS question_competence, question.domain AS question_domain, question.comment AS question_comment 
FROM question 
WHERE ? = question.exercise_id
2018-02-19 07:54:26,016 INFO sqlalchemy.engine.base.Engine (67,)
2018-02-19 07:54:26,01

In [10]:
sc = session.query(Score).all()[123]

2018-02-19 07:54:26,040 INFO sqlalchemy.engine.base.Engine SELECT score.id AS score_id, score.question_id AS score_question_id, score.student_id AS score_student_id, score.value AS score_value 
FROM score
2018-02-19 07:54:26,043 INFO sqlalchemy.engine.base.Engine ()


In [11]:
sc.to_df()

2018-02-19 07:54:26,223 INFO sqlalchemy.engine.base.Engine SELECT student.id AS student_id, student.name AS student_name, student.surname AS student_surname, student.mail AS student_mail, student.commment AS student_commment, student.tribe_id AS student_tribe_id 
FROM student 
WHERE student.id = ?
2018-02-19 07:54:26,225 INFO sqlalchemy.engine.base.Engine (10,)


question_id  student_id  value                          comment competence  \
0            4          10      3  Lire le tableau et le graphique       Cher   

        domain  exercise_id  id_score  is_leveled name_score  score_rate  \
0  4opérations            2         4        True                      0   

               fullname  id_student   name_student surname  tribe_id  
0  ATTOUMANE ALI Fatima          10  ATTOUMANE ALI  Fatima         1